## Ejemplo Captura de Datos

**Tema de Estudio:** "Money FootBall"

El objetivo del presente documento es realizar un análisis a nivel económico de la actualidad del negocio del fútbol profesional a nivel mundial y ver la relación entre resultados e inversión en planteles. Donde se espera obtener:

* Ranking con la estimación de los valores de mercado, salarios y cláusulas de contratos por jugadores, clubes y países en el 2019.
* Ranking de performance de Clubes Europeos más exitosos a nivel continental, desde nuevo formato de UEFA Champions League.
* Conversión a CLP de los resultados obtenidos para realizar análisis comparativos con el mercado chileno (a valor actual).

**Fuente de Datos:**

* Para obtener data de los valores de mercado, salarios y contratos de jugadores en distintos equipos y ligas en el mundo, se utilizó un dataset de kaggle, "FIFA 19 complete player dataset" que contiene la información necesaria para cumplir con el primer punto del objetivo.
* La data del performance de los equipos europeos fue obtenido de un documento PDF del sitio Web de UEFA
* Para valorizar los contratos en CLP, se utilizó el valor de tipo de cambio EUR/CLP de la API de https://mindicador.cl/

In [33]:
import requests as r
import pandas as pd
import numpy as np
from pprint import pprint
import csv
import slate3k as slate
import pymysql

###### Leyendo  archivo -> data.csv, de https://www.kaggle.com/karangadiya/fifa19 correspondiente a "FIFA 19 complete player dataset"

##### Fase Exploratoria -> explorando extructura del archivo data.csv
Data scraped from https://sofifa.com/

In [34]:
file = open('data.csv', 'r')
try:
    data = csv.DictReader(file, delimiter=',')
    for row in data:
        print(row)
finally:
    file.close()

OrderedDict([('\ufeff', '0'), ('ID', '158023'), ('Name', 'L. Messi'), ('Age', '31'), ('Photo', 'https://cdn.sofifa.org/players/4/19/158023.png'), ('Nationality', 'Argentina'), ('Flag', 'https://cdn.sofifa.org/flags/52.png'), ('Overall', '94'), ('Potential', '94'), ('Club', 'FC Barcelona'), ('Club Logo', 'https://cdn.sofifa.org/teams/2/light/241.png'), ('Value', '€110.5M'), ('Wage', '€565K'), ('Special', '2202'), ('Preferred Foot', 'Left'), ('International Reputation', '5'), ('Weak Foot', '4'), ('Skill Moves', '4'), ('Work Rate', 'Medium/ Medium'), ('Body Type', 'Messi'), ('Real Face', 'Yes'), ('Position', 'RF'), ('Jersey Number', '10'), ('Joined', 'Jul 1, 2004'), ('Loaned From', ''), ('Contract Valid Until', '2021'), ('Height', "5'7"), ('Weight', '159lbs'), ('LS', '88+2'), ('ST', '88+2'), ('RS', '88+2'), ('LW', '92+2'), ('LF', '93+2'), ('CF', '93+2'), ('RF', '93+2'), ('RW', '92+2'), ('LAM', '93+2'), ('CAM', '93+2'), ('RAM', '93+2'), ('LM', '91+2'), ('LCM', '84+2'), ('CM', '84+2'), ('RC

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




OrderedDict([('\ufeff', '15550'), ('ID', '231033'), ('Name', 'J. Maguire'), ('Age', '22'), ('Photo', 'https://cdn.sofifa.org/players/4/19/231033.png'), ('Nationality', 'England'), ('Flag', 'https://cdn.sofifa.org/flags/14.png'), ('Overall', '59'), ('Potential', '66'), ('Club', 'Crawley Town'), ('Club Logo', 'https://cdn.sofifa.org/teams/2/light/110890.png'), ('Value', '€180K'), ('Wage', '€1K'), ('Special', '1505'), ('Preferred Foot', 'Left'), ('International Reputation', '1'), ('Weak Foot', '2'), ('Skill Moves', '2'), ('Work Rate', 'Medium/ Medium'), ('Body Type', 'Lean'), ('Real Face', 'No'), ('Position', 'LB'), ('Jersey Number', '16'), ('Joined', ''), ('Loaned From', 'Fleetwood Town'), ('Contract Valid Until', 'Jan 1, 2019'), ('Height', "5'10"), ('Weight', '154lbs'), ('LS', '48+2'), ('ST', '48+2'), ('RS', '48+2'), ('LW', '52+2'), ('LF', '50+2'), ('CF', '50+2'), ('RF', '50+2'), ('RW', '52+2'), ('LAM', '49+2'), ('CAM', '49+2'), ('RAM', '49+2'), ('LM', '53+2'), ('LCM', '49+2'), ('CM', 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



###### Seleccionando la Data a utilizar para el análisis.

**Campos a utilizar:** Name, Age, Nationality, Club, Value, Wage, Joined, Contract Valid Until, Release Clause

**Donde:**
* Name -> Nombre del jugador.
* Age -> Edad del jugador.
* Nationality -> Nacionalidad del jugador.
* Club -> Club dueño del pase del jugador.
* Value -> Valor actual de mercado del jugador
* Wage -> Salario actual del jugador
* Joined -> Fecha de ingreso del jugador a su club actual.
* Contract Valid Until -> Fecha de finalización del contrato del jugador con su club.
* Release Clause -> Valor de la cláusula de liberación del jugador con su club.

In [35]:
with open('data.csv', 'r') as csvfile:
    reader = csv.DictReader(csvfile)
    
    for row in reader:
        print(row['Name'],"-",row['Age'],"-",row['Nationality'],"-",row['Club'],"-",row['Value'],"-",row['Wage'],"-",
              row['Joined'],"-",row['Contract Valid Until'],"-",row['Release Clause'])

L. Messi - 31 - Argentina - FC Barcelona - €110.5M - €565K - Jul 1, 2004 - 2021 - €226.5M
Cristiano Ronaldo - 33 - Portugal - Juventus - €77M - €405K - Jul 10, 2018 - 2022 - €127.1M
Neymar Jr - 26 - Brazil - Paris Saint-Germain - €118.5M - €290K - Aug 3, 2017 - 2022 - €228.1M
De Gea - 27 - Spain - Manchester United - €72M - €260K - Jul 1, 2011 - 2020 - €138.6M
K. De Bruyne - 27 - Belgium - Manchester City - €102M - €355K - Aug 30, 2015 - 2023 - €196.4M
E. Hazard - 27 - Belgium - Chelsea - €93M - €340K - Jul 1, 2012 - 2020 - €172.1M
L. Modrić - 32 - Croatia - Real Madrid - €67M - €420K - Aug 1, 2012 - 2020 - €137.4M
L. Suárez - 31 - Uruguay - FC Barcelona - €80M - €455K - Jul 11, 2014 - 2021 - €164M
Sergio Ramos - 32 - Spain - Real Madrid - €51M - €380K - Aug 1, 2005 - 2020 - €104.6M
J. Oblak - 25 - Slovenia - Atlético Madrid - €68M - €94K - Jul 16, 2014 - 2021 - €144.5M
R. Lewandowski - 29 - Poland - FC Bayern München - €77M - €205K - Jul 1, 2014 - 2021 - €127.1M
T. Kroos - 28 - German

Iago Aspas - 30 - Spain - RC Celta - €30M - €45K - Jul 1, 2015 - 2022 - €63M
B. Leno - 26 - Germany - Arsenal - €27M - €115K - Jul 1, 2018 - 2023 - €53.3M
N. Matić - 29 - Serbia - Manchester United - €24M - €165K - Jul 31, 2017 - 2020 - €44.4M
L. Hrádecký - 28 - Finland - Bayer 04 Leverkusen - €22M - €74K - Jul 1, 2018 - 2023 - €37.4M
Illarramendi - 28 - Spain - Real Sociedad - €31M - €51K - Aug 26, 2015 - 2023 - €65.1M
K. Walker - 28 - England - Manchester City - €24.5M - €165K - Jul 14, 2017 - 2022 - €45.3M
I. Gündoğan - 27 - Germany - Manchester City - €32M - €175K - Jul 1, 2016 - 2020 - €59.2M
José Callejón - 31 - Spain - Napoli - €27.5M - €105K - Jul 11, 2013 - 2020 - €46.8M
A. Di María - 30 - Argentina - Paris Saint-Germain - €29.5M - €125K - Aug 6, 2015 - 2021 - €54.6M
M. Mandžukić - 32 - Croatia - Juventus - €25M - €160K - Jul 1, 2015 - 2020 - €41.3M
Willian - 29 - Brazil - Chelsea - €30.5M - €175K - Aug 28, 2013 - 2020 - €56.4M
Sergio Asenjo - 29 - Spain - Villarreal CF - €24M

J. Cillessen - 29 - Netherlands - FC Barcelona - €18M - €135K - Aug 25, 2016 - 2021 - €38.3M
W. Ben Yedder - 27 - France - Sevilla FC - €23.5M - €28K - Jul 30, 2016 - 2021 - €49.4M
C. Bakambu - 27 - DR Congo - Beijing Sinobo Guoan FC - €26M - €33K - Jan 17, 2018 - 2021 - €59.2M
Pablo Sarabia - 26 - Spain - Sevilla FC - €26M - €26K - Jul 1, 2016 - 2020 - €56.6M
W. Zaha - 25 - Ivory Coast - Crystal Palace - €28.5M - €78K - Feb 2, 2015 - 2023 - €56.3M
Luis Alberto - 25 - Spain - Lazio - €28.5M - €67K - Aug 31, 2016 - 2022 - €50.6M
Jonathan Viera - 28 - Spain - Beijing Sinobo Guoan FC - €22.5M - €31K - Feb 19, 2018 - 2020 - €49.5M
Bartra - 27 - Spain - Real Betis - €21M - €32K - Jan 30, 2018 - 2023 - €45.7M
S. Coates - 27 - Uruguay - Sporting CP - €21M - €19K - Jan 31, 2017 - 2022 - €43.6M
Willian José - 26 - Brazil - Real Sociedad - €26.5M - €44K - Jul 31, 2016 - 2024 - €57.6M
Mário Fernandes - 27 - Russia - PFC CSKA Moscow - €18.5M - €1K - Jul 1, 2012 - 2022 - €40.7M
Víctor Ruiz - 29 - S

H. Herrera - 28 - Mexico - FC Porto - €17.5M - €20K - Jul 1, 2013 - 2019 - €35M
Raffael - 33 - Brazil - Borussia Mönchengladbach - €11M - €41K - Jul 1, 2013 - 2019 - €18.7M
Nani - 31 - Portugal - Sporting CP - €15.5M - €19K - Jul 11, 2018 - 2020 - €31M
J. Milner - 32 - England - Liverpool - €13.5M - €120K - Jul 1, 2015 - 2020 - €25.7M
J. Mathieu - 34 - France - Sporting CP - €5.5M - €18K - Jul 7, 2017 - 2019 - €11M
Joaquín - 36 - Spain - Real Betis - €6M - €24K - Sep 1, 2015 - 2020 - €12.6M
M. Gómez - 21 - Uruguay - RC Celta - €20.5M - €25K - Jul 1, 2017 - 2022 - €44.6M
K. Havertz - 19 - Germany - Bayer 04 Leverkusen - €22M - €32K - Jul 1, 2016 - 2022 - €41.8M
T. Ndombele - 21 - France - Olympique Lyonnais - €22.5M - €51K - Jul 1, 2018 - 2023 - €47.3M
H. Aouar - 20 - France - Olympique Lyonnais - €23.5M - €51K - Jul 1, 2016 - 2023 - €49.4M
Carlos Soler - 21 - Spain - Valencia CF - €21M - €31K - Jul 1, 2015 - 2021 - €48.3M
Odriozola - 22 - Spain - Real Madrid - €18.5M - €115K - Jul 5, 2

A. Gignac - 32 - France - Tigres U.A.N.L. - €12M - €70K - Jun 18, 2015 - 2019 - €19.2M
M. Gómez - 32 - Germany - VfB Stuttgart - €12M - €46K - Jan 1, 2018 - 2020 - €20.4M
I. Akinfeev - 32 - Russia - PFC CSKA Moscow - €8.5M - €1K - Jan 1, 2002 - 2022 - €18.7M
I. Denisov - 34 - Russia - Lokomotiv Moscow - €4.5M - €1K - Aug 15, 2013 - 2019 - €9.4M
Juanfran - 33 - Spain - Atlético Madrid - €5.5M - €53K - Jan 1, 2011 - 2019 - €11.3M
Diego López - 36 - Spain - RCD Espanyol - €2M - €17K - Jul 1, 2017 - 2020 - €4.2M
Santi Cazorla - 33 - Spain - Villarreal CF - €8.5M - €39K - Aug 6, 2018 - 2019 - €17.9M
Jesús Navas - 32 - Spain - Sevilla FC - €11.5M - €22K - Jul 28, 2017 - 2021 - €24.2M
J. Mascherano - 34 - Argentina - Hebei China Fortune FC - €4.5M - €20K - Jan 26, 2018 - 2019 - €9.7M
A. Mirante - 34 - Italy - Roma - €6M - €51K - Jul 1, 2018 - 2021 - €10.2M
D. Srna - 36 - Croatia - Cagliari - €1.7M - €27K - Aug 22, 2018 - 2019 - €2.9M
B. Schweinsteiger - 33 - Germany - Chicago Fire - €6M - €11

...

I. Al Otaibi - 21 - Saudi Arabia - Al Taawoun - €100K - €2K - Jul 1, 2017 - 2021 - €185K
R. Kawai - 39 - Japan - Hokkaido Consadole Sapporo - €0 - €1K - Jan 1, 2011 - 2021 - 
Yu Hao - 20 - China PR - Shanghai SIPG FC - €80K - €2K - Jul 15, 2016 - 2019 - €192K
Jeong Chung Yeob - 20 - Korea Republic - Daegu FC - €130K - €1K - Jul 1, 2017 - 2021 - €244K
M. Al Nakhli - 22 - Saudi Arabia - Al Fateh - €110K - €3K - Aug 14, 2018 - 2021 - €204K
Liu Yu - 23 - China PR - Changchun Yatai FC - €60K - €1K - Feb 1, 2015 - 2021 - €134K
D. Revan - 17 - England - Aston Villa - €110K - €1K - Jul 1, 2018 - 2020 - €278K
W. Longbottom - 19 - England - Doncaster Rovers - €80K - €1K - Mar 31, 2016 - 2020 - €156K
R. Treacy - 19 - Republic of Ireland - Dundalk - €70K - €1K - Feb 1, 2018 - 2018 - €123K
J. Bartels - 19 - Germany - 1. FC Köln - €90K - €1K - Jul 1, 2018 - 2020 - €191K
M. Hayashi - 21 - Japan - Gamba Osaka - €80K - €1K - Jan 1, 2015 - 2021 - €116K
A. Rose - 19 - Jamaica - Grimsby Town - €100K - €1K

R. Fujimura - 19 - Japan - Hokkaido Consadole Sapporo - €80K - €1K - Jan 1, 2018 - 2021 - €116K
S. Pryce - 18 - England - Swindon Town - €80K - €1K - Jul 1, 2018 - 2019 - €156K
G. Zuñiga - 18 - Chile - CD O'Higgins - €60K - €1K - Jan 1, 2017 - 2021 - €93K
T. Romboli - 19 - Italy - Livorno - €90K - €1K - Jul 1, 2016 - 2021 - €196K
S. Bohan - 17 - Republic of Ireland - Bohemian FC - €80K - €1K - Apr 27, 2018 - 2018 - €174K
F. Gemmi - 21 - Italy - Livorno - €60K - €1K - Jul 1, 2016 - 2021 - €105K
J. Brendieck - 19 - Germany - MSV Duisburg - €90K - €1K - Jul 1, 2018 - 2019 - €200K
A. Mahlonoko - 16 - South Africa - Orlando Pirates - €100K - €1K - Aug 3, 2018 - 2020 - €278K
L. Simpson - 23 - England - Macclesfield Town - €50K - €1K - Aug 2, 2018 - 2022 - €98K
A. Ahl Holmström - 19 - Sweden - Kalmar FF - €110K - €1K - Sep 30, 2018 - 2020 - €206K
E. Gumbs - 20 - England - Tranmere Rovers - €90K - €1K - Aug 12, 2014 - 2023 - €214K
G. Tsitaishvili - 17 - Ukraine - Dynamo Kyiv - €100K - €1K - Ju

L. Brown - 19 - Scotland - Motherwell - €80K - €1K - Jul 1, 2017 - 2019 - €220K
E. McCue - 17 - Sweden - Houston Dynamo - €70K - €1K - Oct 30, 2018 - 2021 - €175K
A. Skindlo - 19 - Norway - FK Bodø/Glimt - €60K - €1K - Jun 27, 2018 - 2021 - €87K
K. Konstandopoulos - 19 - Australia - Adelaide United - €80K - €1K - Sep 22, 2017 - 2019 - €150K
K. Salazar - 19 - Colombia - Atlético Huila - €70K - €1K - Jul 6, 2018 - 2021 - €138K
S. Sarri - 17 - Italy - Foggia - €70K - €1K - Jul 1, 2018 - 2021 - €182K
O. Schindler - 18 - Hungary - SC Paderborn 07 - €70K - €1K - Jul 1, 2018 - 2019 - €152K
M. Arena - 19 - Italy - Foggia - €50K - €1K - Jul 1, 2018 - 2021 - €90K
L. Cavallini - 18 - Italy - Foggia - €80K - €1K - Jul 1, 2018 - 2021 - €178K
B. Hvidt - 18 - Denmark - Aarhus GF - €80K - €1K - May 7, 2016 - 2019 - €150K
S. Pollock - 17 - England - Northampton Town - €70K - €1K - Sep 29, 2018 - 2020 - €166K
J. Baxter - 17 - England - Preston North End - €70K - €1K - Jul 1, 2018 - 2021 - €177K
T. Stead

Hong Hyeon Seok - 19 - Korea Republic - SpVgg Unterhaching - €50K - €1K - Jul 1, 2018 - 2019 - €104K
C. Walsh - 17 - Republic of Ireland - Bray Wanderers - €50K - €1K - Feb 1, 2017 - 2018 - €128K
T. Miyamoto - 19 - Japan - Kashiwa Reysol - €60K - €1K - Jan 1, 2018 - 2021 - €113K
R. Hurley - 18 - Republic of Ireland - Cork City - €40K - €1K - Oct 5, 2018 - 2018 - €70K
Gao Dalun - 21 - China PR - Jiangsu Suning FC - €40K - €2K - Jan 1, 2018 - 2022 - €94K
R. Hackett-Fairchild - 20 - England - Charlton Athletic - €70K - €1K - Oct 20, 2016 - 2019 - €166K
L. Klitten - 18 - Denmark - Aalborg BK - €50K - €1K - Apr 18, 2018 - 2021 - €94K
Zhang Jingyi - 20 - China PR - Jiangsu Suning FC - €30K - €1K - Jan 1, 2018 - 2022 - €71K
T. Brownsword - 18 - England - Morecambe - €50K - €1K - Feb 25, 2017 - 2019 - €119K
Zhang Gong - 26 - China PR - Guangzhou R&F; FC - €30K - €2K - Jan 1, 2017 - 2021 - €67K
J. García - 20 - Mexico - Santos Laguna - €40K - €1K - Jul 1, 2017 - 2021 - €76K
O. Dzonlagic - 23 - 

C. Maher - 17 - Republic of Ireland - Bray Wanderers - €50K - €1K - Jan 1, 2017 - 2018 - €109K
Y. Góez - 18 - Colombia - Atlético Nacional - €50K - €1K - Sep 8, 2018 - 2021 - €101K
K. Pilkington - 44 - England - Cambridge United - €0 - €1K - Aug 17, 2018 - 2023 - 
D. Horton - 18 - England - Lincoln City - €40K - €1K - Nov 4, 2017 - 2021 - €78K
E. Tweed - 19 - Republic of Ireland - Derry City - €50K - €1K - Feb 23, 2018 - 2018 - €88K
Zhang Yufeng - 20 - China PR - Beijing Renhe FC - €60K - €1K - Jul 11, 2016 - 2019 - €167K
C. Ehlich - 19 - Germany - SpVgg Unterhaching - €40K - €1K - Jul 1, 2017 - 2020 - €66K
L. Collins - 17 - Wales - Newport County - €60K - €1K - Jul 1, 2017 - 2021 - €143K
A. Kaltner - 18 - Germany - SpVgg Unterhaching - €60K - €1K - Jul 1, 2017 - 2020 - €125K
L. Watkins - 18 - England - Cambridge United - €60K - €1K - Jul 1, 2018 - 2021 - €165K
J. Norville-Williams - 18 - England - Cambridge United - €50K - €1K - Jul 1, 2018 - 2021 - €119K
S. Squire - 18 - England - Ca

Almacenando data de jugadores en Diccionario de datos "jugadores"

In [36]:
jugadores = {
    'Name':[],
    'Age':[],
    'Nationality':[],
    'Club':[],
    'Value':[],
    'Wage':[],
    'Joined':[],
    'Contract Valid Until':[],
    'Release Clause':[]
}

with open('data.csv', 'r') as csvfile:
    reader = csv.DictReader(csvfile)
    
    for row in reader:
        df = (row['Name'],row['Age'],row['Nationality'],row['Club'],row['Value'],row['Wage'], row['Joined'],
              row['Contract Valid Until'],row['Release Clause'])
        
        jugadores['Name'].append(df[0])
        jugadores['Age'].append(df[1])
        jugadores['Nationality'].append(df[2])
        jugadores['Club'].append(df[3])
        jugadores['Value'].append(df[4])
        jugadores['Wage'].append(df[5])
        jugadores['Joined'].append(df[6])
        jugadores['Contract Valid Until'].append(df[7])
        jugadores['Release Clause'].append(df[8])

Asignando data de jugadores en dataframe "frameJugadores"</p>
Limpiando data necesaria

In [37]:
frameJugadores = pd.DataFrame(jugadores)

# renombrando las columnas con data de dinero, para eliminar el signo € de cada valor y asignarles el datatype ideal.
frameJugadores.rename(columns={'Value':'Value(€)', 'Wage':'Wage(€)','Release Clause':'Release Clause(€)'}, inplace=True) 

# Limpiando signo € de cada valor monetario.
frameJugadores['Value(€)'] = frameJugadores['Value(€)'].str.lstrip('€')
frameJugadores['Wage(€)'] = frameJugadores['Wage(€)'].str.lstrip('€')
frameJugadores['Release Clause(€)'] = frameJugadores['Release Clause(€)'].str.lstrip('€')

print(frameJugadores)

                       Name Age          Nationality                    Club  \
0                  L. Messi  31            Argentina            FC Barcelona   
1         Cristiano Ronaldo  33             Portugal                Juventus   
2                 Neymar Jr  26               Brazil     Paris Saint-Germain   
3                    De Gea  27                Spain       Manchester United   
4              K. De Bruyne  27              Belgium         Manchester City   
5                 E. Hazard  27              Belgium                 Chelsea   
6                 L. Modrić  32              Croatia             Real Madrid   
7                 L. Suárez  31              Uruguay            FC Barcelona   
8              Sergio Ramos  32                Spain             Real Madrid   
9                  J. Oblak  25             Slovenia         Atlético Madrid   
10           R. Lewandowski  29               Poland       FC Bayern München   
11                 T. Kroos  28         

Removiendo abreviatura de miles K(10^3) y millones M(10^6) para columnas con data en Euros

In [38]:
# Usando range arbitrario de len(frameJugadores['Value(€)'])
for i in range(0,len(frameJugadores['Value(€)'])) :
    # para Value(€)
    if str(frameJugadores['Value(€)'][i]).endswith('K'): # para remover abreviatura de miles 
        frameJugadores['Value(€)'][i] = frameJugadores['Value(€)'][i].replace('K','') # removiendo abreviatura
        frameJugadores['Value(€)'][i] = float(frameJugadores['Value(€)'][i]) # asignando data type apropiado
        frameJugadores['Value(€)'][i] = frameJugadores['Value(€)'][i] * 10**3 # para obtener valor numeral real
    if str(frameJugadores['Value(€)'][i]).endswith('M'): # para remover abreviatura de millones
        frameJugadores['Value(€)'][i] = frameJugadores['Value(€)'][i].replace('M','') # removiendo abreviatura
        frameJugadores['Value(€)'][i] = float(frameJugadores['Value(€)'][i]) # asignando data type apropiado
        frameJugadores['Value(€)'][i] = frameJugadores['Value(€)'][i] * 10**6 # para obtener valor numeral real
    
    # para Wage(€), limpieza idem que Value(€)
    if str(frameJugadores['Wage(€)'][i]).endswith('K'):
        frameJugadores['Wage(€)'][i] = frameJugadores['Wage(€)'][i].replace('K','')
        frameJugadores['Wage(€)'][i] = float(frameJugadores['Wage(€)'][i])
        frameJugadores['Wage(€)'][i] = frameJugadores['Wage(€)'][i] * 10**3
    if str(frameJugadores['Wage(€)'][i]).endswith('M'):
        frameJugadores['Wage(€)'][i] = frameJugadores['Wage(€)'][i].replace('M','')
        frameJugadores['Wage(€)'][i] = float(frameJugadores['Wage(€)'][i])
        frameJugadores['Wage(€)'][i] = frameJugadores['Wage(€)'][i] * 10**6
        
    # para Release Clause(€), limpieza idem que Value(€)
    if str(frameJugadores['Release Clause(€)'][i]).endswith('K'):
        frameJugadores['Release Clause(€)'][i] = frameJugadores['Release Clause(€)'][i].replace('K','')
        frameJugadores['Release Clause(€)'][i] = float(frameJugadores['Release Clause(€)'][i])
        frameJugadores['Release Clause(€)'][i] = frameJugadores['Release Clause(€)'][i] * 10**3
    if str(frameJugadores['Release Clause(€)'][i]).endswith('M'):
        frameJugadores['Release Clause(€)'][i] = frameJugadores['Release Clause(€)'][i].replace('M','')
        frameJugadores['Release Clause(€)'][i] = float(frameJugadores['Release Clause(€)'][i])
        frameJugadores['Release Clause(€)'][i] = frameJugadores['Release Clause(€)'][i] * 10**6

print(frameJugadores)     

                       Name Age          Nationality                    Club  \
0                  L. Messi  31            Argentina            FC Barcelona   
1         Cristiano Ronaldo  33             Portugal                Juventus   
2                 Neymar Jr  26               Brazil     Paris Saint-Germain   
3                    De Gea  27                Spain       Manchester United   
4              K. De Bruyne  27              Belgium         Manchester City   
5                 E. Hazard  27              Belgium                 Chelsea   
6                 L. Modrić  32              Croatia             Real Madrid   
7                 L. Suárez  31              Uruguay            FC Barcelona   
8              Sergio Ramos  32                Spain             Real Madrid   
9                  J. Oblak  25             Slovenia         Atlético Madrid   
10           R. Lewandowski  29               Poland       FC Bayern München   
11                 T. Kroos  28         

**Leyendo data de documentos PDF's** del sitio Web de UEFA para ver performance histórico de equipos a nivel europeo -> https://www.uefa.com/uefachampionsleague/statistics/all-time/

In [39]:
pdf = '2285688_DOWNLOAD.pdf' # UEFA CHAMPIONS LEAGUE STATISTICS HANDBOOK 2018/19 - 1. FACTS & FIGURES

##### Fase Exploratoria -> explorando extructura de archico pdf
Leyendo tabla **RANKINGS: All-time ranking by club** (pag 2)

In [40]:
with open (pdf, 'rb') as f:
    doc = slate.PDF(f)
    page = doc[1]
    lista = page.split('\n')
    print(type(page))
    teams = lista[3:666] # Ranking Primeros 48 Equipos
    print(teams)

<class 'str'>
['', 'Pos ', '', 'Club ', '', 'Country ', '', 'Part ', '', 'Titles ', '', '1 ', '2 ', '3 ', '4 ', '5 ', '6 ', '7 ', '8 ', '9 ', '10 ', '11 ', '12 ', '13 ', '14 ', '15 ', '16 ', '17 ', '18 ', '19 ', '20 ', '21 ', '22 ', '23 ', '24 ', '25 ', '26 ', '27 ', '28 ', '29 ', '30 ', '31 ', '32 ', '33 ', '34 ', '35 ', '36 ', '37 ', '38 ', '39 ', '40 ', '41 ', '42 ', '43 ', '44 ', '45 ', '46 ', '47 ', '48 ', '', 'Real Madrid CF ', 'FC Barcelona ', 'FC Bayern München ', 'Manchester United FC ', 'Juventus ', 'Arsenal FC ', 'FC Porto ', 'Chelsea FC ', 'AC Milan ', 'Olympique Lyonnais ', 'Liverpool FC ', 'FC Internazionale Milano ', 'Borussia Dortmund ', 'Paris Saint-Germain ', 'AFC Ajax ', 'Valencia CF ', 'Club Atlético de Madrid ', 'AS Roma ', 'Olympiacos FC ', 'SL Benfica ', 'Bayer 04 Leverkusen ', 'PSV Eindhoven ', 'FC Dynamo Kyiv ', 'Galatasaray AŞ ', 'FC Shakhtar Donetsk ', 'Manchester City FC ', 'AS Monaco FC ', 'FC Schalke 04 ', 'Panathinaikos FC ', 'FC Spartak Moskva ', 'RC Dep

Eliminando campos vacios de lectura de equipos

In [41]:
def elimina(lista):
    nueva_lista = []
    
    for line in lista:
        linea = line.strip()
        if linea == '':
            continue
        nueva_lista.append(linea)
    return nueva_lista

Ordenando formato de **RANKINGS: All-time ranking by club (Champions League 1993-2019)**

In [42]:
with open (pdf, 'rb') as f:
    doc = slate.PDF(f)
    page = doc[1]
    lista = page.split('\n')
    pos = elimina(lista[13:62]) # Position - int
    team = elimina(lista[63:112]) # String
    country = elimina(lista[112:160]) # String
    part = elimina(lista[160:209]) # Participations - uint
    titles = elimina(lista[209:258]) # uint
    pld = elimina(lista[260:309]) # Matches played - uint
    win = elimina(lista[311:360]) # Matches won - uint
    draw = elimina(lista[362:411]) # Matches drawn - uint
    lost = elimina(lista[413:462]) # Matches lost - uint
    gf = elimina(lista[464:514]) # Goals for - uint
    ga = elimina(lista[515:565]) # Goals against - int
    pts = elimina(lista[566:616]) # Points (2 for a win, 1 for a draw) - uint
    gd = elimina(lista[617:666]) # Goals for - Goals against - int
    
    combinados = zip(pos,team,country,part,titles,pld,win,draw,lost,gf,ga,pts,gd)
    for c in combinados:
        print(c)

('1', 'Real Madrid CF', 'ESP', '23', '7', '259', '156', '49', '54', '551', '281', '361', '270')
('2', 'FC Barcelona', 'ESP', '23', '4', '248', '146', '59', '43', '502', '241', '351', '261')
('3', 'FC Bayern München', 'GER', '22', '2', '241', '132', '53', '56', '457', '253', '317', '204')
('4', 'Manchester United FC', 'ENG', '22', '2', '224', '118', '56', '50', '373', '210', '292', '163')
('5', 'Juventus', 'ITA', '19', '1', '190', '92', '51', '47', '292', '189', '235', '103')
('6', 'Arsenal FC', 'ENG', '19', '0', '177', '83', '41', '53', '281', '205', '207', '76')
('7', 'FC Porto', 'POR', '23', '1', '188', '80', '46', '62', '253', '220', '206', '33')
('8', 'Chelsea FC', 'ENG', '15', '1', '156', '77', '45', '34', '266', '142', '199', '124')
('9', 'AC Milan', 'ITA', '17', '3', '165', '74', '49', '42', '231', '156', '197', '75')
('10', 'Olympique Lyonnais', 'FRA', '15', '0', '126', '54', '34', '38', '200', '151', '142', '49')
('11', 'Liverpool FC', 'ENG', '11', '2', '114', '55', '31', '28'

Almacenando data de equipos en Diccionario de datos "equipos"

In [43]:
equipos = {
    'pos':[],
    'team':[],
    'country':[],
    'part':[],
    'titles':[],
    'pld':[],
    'win':[],
    'draw':[],
    'lost':[],
    'gf':[],
    'ga':[],
    'pts':[],
    'gd':[]
}

with open (pdf, 'rb') as f:
    doc = slate.PDF(f)
    page = doc[1]
    lista = page.split('\n')
    pos = elimina(lista[13:62]) # Position - uint
    team = elimina(lista[63:112]) # String
    country = elimina(lista[112:160]) # String
    part = elimina(lista[160:209]) # Participations - uint
    titles = elimina(lista[209:258]) # uint
    pld = elimina(lista[260:309]) # Matches played - uint
    win = elimina(lista[311:360]) # Matches won - uint
    draw = elimina(lista[362:411]) # Matches drawn - uint
    lost = elimina(lista[413:462]) # Matches lost - uint
    gf = elimina(lista[464:514]) # Goals for - uint
    ga = elimina(lista[515:565]) # Goals against - int
    pts = elimina(lista[566:616]) # Points (2 for a win, 1 for a draw) - uint
    gd = elimina(lista[617:666]) # Goals for - Goals against - int
    
    combinados = zip(pos,team,country,part,titles,pld,win,draw,lost,gf,ga,pts,gd)
    for c in combinados:
        equipos['pos'].append(c[0])
        equipos['team'].append(c[1])
        equipos['country'].append(c[2])
        equipos['part'].append(c[3])
        equipos['titles'].append(c[4])
        equipos['pld'].append(c[5])
        equipos['win'].append(c[6])
        equipos['draw'].append(c[7])
        equipos['lost'].append(c[8])
        equipos['gf'].append(c[9])
        equipos['ga'].append(c[10])
        equipos['pts'].append(c[11])
        equipos['gd'].append(c[12])

Asignando data de jugadores en dataframe "frameEquipos"

In [44]:
frameEquipos = pd.DataFrame(equipos)
print(frameEquipos)

   pos                        team country part titles  pld  win draw lost  \
0    1              Real Madrid CF     ESP   23      7  259  156   49   54   
1    2                FC Barcelona     ESP   23      4  248  146   59   43   
2    3           FC Bayern München     GER   22      2  241  132   53   56   
3    4        Manchester United FC     ENG   22      2  224  118   56   50   
4    5                    Juventus     ITA   19      1  190   92   51   47   
5    6                  Arsenal FC     ENG   19      0  177   83   41   53   
6    7                    FC Porto     POR   23      1  188   80   46   62   
7    8                  Chelsea FC     ENG   15      1  156   77   45   34   
8    9                    AC Milan     ITA   17      3  165   74   49   42   
9   10          Olympique Lyonnais     FRA   15      0  126   54   34   38   
10  11                Liverpool FC     ENG   11      2  114   55   31   28   
11  12    FC Internazionale Milano     ITA   12      1  111   52

Asignando datatypes idóneos para futuros cálculos

In [45]:
frameEquipos['pos'] = frameEquipos['pos'].astype('uint')
frameEquipos['part'] = frameEquipos['part'].astype('uint')
frameEquipos['titles'] = frameEquipos['titles'].astype('uint')
frameEquipos['pld'] = frameEquipos['pld'].astype('uint')
frameEquipos['win'] = frameEquipos['win'].astype('uint')
frameEquipos['draw'] = frameEquipos['draw'].astype('uint')
frameEquipos['lost'] = frameEquipos['lost'].astype('uint')
frameEquipos['gf'] = frameEquipos['gf'].astype('uint')
frameEquipos['ga'] = frameEquipos['ga'].astype('int')
frameEquipos['pts'] = frameEquipos['pts'].astype('uint')
frameEquipos['gd'] = frameEquipos['gd'].astype('int')

Homologando Nombre de Clubes entre frameEquipos y frameJugadores (según registro de frameJugadores)</p>
Para los 20 primeros clubes del ranking de ganadores de europa.

In [46]:
frameEquipos = frameEquipos[frameEquipos['pos'] <= 20]

frameEquipos['team'] = frameEquipos['team'].map(lambda x: x.rstrip(' FC'))
frameEquipos["team"]= frameEquipos["team"].replace("Real Madrid CF", "Real Madrid") 
frameEquipos["team"]= frameEquipos["team"].replace("AC Milan", "Milan")
frameEquipos["team"]= frameEquipos["team"].replace("FC Internazionale Milano", "Inter")
frameEquipos["team"]= frameEquipos["team"].replace("Club Atlético de Madrid", "Atlético Madrid")
frameEquipos["team"]= frameEquipos["team"].replace("AFC Ajax", "Ajax")
frameEquipos["team"]= frameEquipos["team"].replace("AS Roma", "Roma")
frameEquipos["team"]= frameEquipos["team"].replace("Olympiacos", "Olympiacos CFP")

print(frameEquipos)

    pos                 team country  part  titles  pld  win  draw  lost   gf  \
0     1          Real Madrid     ESP    23       7  259  156    49    54  551   
1     2         FC Barcelona     ESP    23       4  248  146    59    43  502   
2     3    FC Bayern München     GER    22       2  241  132    53    56  457   
3     4    Manchester United     ENG    22       2  224  118    56    50  373   
4     5             Juventus     ITA    19       1  190   92    51    47  292   
5     6              Arsenal     ENG    19       0  177   83    41    53  281   
6     7             FC Porto     POR    23       1  188   80    46    62  253   
7     8              Chelsea     ENG    15       1  156   77    45    34  266   
8     9                Milan     ITA    17       3  165   74    49    42  231   
9    10   Olympique Lyonnais     FRA    15       0  126   54    34    38  200   
10   11            Liverpool     ENG    11       2  114   55    31    28  194   
11   12                Inter

**Merge:** Entre data frames frameJugadores y frameEquipos seleccionando campos necesarios para el insert dentro
de la BBDD de almacenamiento.

In [47]:
Money_FootBall= pd.merge(frameJugadores[['Name','Nationality','Club','Value(€)','Wage(€)','Release Clause(€)']],
                         frameEquipos[['team','pos']],
                         left_on = 'Club',
                         right_on='team')

In [48]:
Money_FootBall

Name  Nationality            Club   Value(€) Wage(€)  \
0                 L. Messi    Argentina    FC Barcelona  1.105e+08  565000   
1                L. Suárez      Uruguay    FC Barcelona      8e+07  455000   
2            M. ter Stegen      Germany    FC Barcelona    5.8e+07  240000   
3          Sergio Busquets        Spain    FC Barcelona   5.15e+07  315000   
4                 Coutinho       Brazil    FC Barcelona   6.95e+07  340000   
5                S. Umtiti       France    FC Barcelona    5.7e+07  205000   
6               Jordi Alba        Spain    FC Barcelona    3.8e+07  250000   
7               I. Rakitić      Croatia    FC Barcelona   4.65e+07  260000   
8                    Piqué        Spain    FC Barcelona    3.4e+07  240000   
9                 A. Vidal        Chile    FC Barcelona    2.6e+07  205000   
10              O. Dembélé       France    FC Barcelona      4e+07  155000   
11           Sergi Roberto        Spain    FC Barcelona   2.65e+07  170000   
12                  Arthur       Brazil    FC Barcelona   3.25e+07  125000   
13                  Malcom       Brazil    FC Barcelona   3.15e+07  140000   
14              C. Lenglet       France    FC Barcelona    2.6e+07  135000   
15                 Rafinha       Brazil    FC Barcelona   2.95e+07  165000   
16            J. Cillessen  Netherlands    FC Barcelona    1.8e+07  135000   
17           Nélson Semedo     Portugal    FC Barcelona      2e+07  125000   
18            Denis Suárez        Spain    FC Barcelona   1.75e+07  120000   
19                   Munir        Spain    FC Barcelona   1.25e+07  115000   
20            T. Vermaelen      Belgium    FC Barcelona      5e+06  110000   
21            Sergi Samper        Spain    FC Barcelona    4.8e+06   69000   
22                   Aleñá        Spain    FC Barcelona      6e+06   58000   
23                M. Wagué      Senegal    FC Barcelona    1.6e+06   20000   
24              Riqui Puig        Spain    FC Barcelona    2.1e+06   24000   
25          Oriol Busquets        Spain    FC Barcelona    1.5e+06   14000   
26               Abel Ruiz        Spain    FC Barcelona    1.6e+06   21000   
27                 Miranda        Spain    FC Barcelona    1.2e+06   12000   
28                   Chumi        Spain    FC Barcelona      1e+06   11000   
29            Jorge Cuenca        Spain    FC Barcelona     850000   11000   
..                     ...          ...             ...        ...     ...   
538                N. Lang  Netherlands            Ajax     950000    3000   
539         J. Ekkelenkamp  Netherlands            Ajax     950000    2000   
540         Daniel Podence     Portugal  Olympiacos CFP    1.4e+07    1000   
541              B. Natcho       Israel  Olympiacos CFP    9.5e+06    1000   
542           K. Fortounis       Greece  Olympiacos CFP    1.1e+07    1000   
543                José Sá     Portugal  Olympiacos CFP    8.5e+06    1000   
544  L. Christodoulopoulos       Greece  Olympiacos CFP      7e+06    1000   
545              Guilherme       Brazil  Olympiacos CFP    6.5e+06    1000   
546        O. Elabdellaoui       Norway  Olympiacos CFP    6.5e+06    1000   
547             J. Vuković       Serbia  Olympiacos CFP    4.9e+06    1000   
548         I. Fetfatzidis       Greece  Olympiacos CFP      7e+06    1000   
549               Guerrero        Spain  Olympiacos CFP      6e+06    1000   
550              A. Hassan        Egypt  Olympiacos CFP    7.5e+06    1000   
551          A. Gianniotis       Greece  Olympiacos CFP      5e+06    1000   
552               F. Pardo     Colombia  Olympiacos CFP    4.2e+06    1000   
553           V. Torosidis       Greece  Olympiacos CFP    1.5e+06    1000   
554               P. Cissé      Senegal  Olympiacos CFP    4.4e+06    1000   
555              M. Camara       Guinea  Olympiacos CFP    4.4e+06    1000   
556             L. Koutris       Greece  Olympiacos CFP    2.8e+06    1000   
557            K. Tsimikas       Greece  Oly

#### Consulta de Indicadores Económicos -> https://mindicador.cl/
##### Fase Exploratoria -> explorando extructura de la api

In [49]:
response = r.get("https://mindicador.cl/api")

In [50]:
print(response.status_code)

200


In [51]:
if response.status_code == 200:
    contenido = response.json()
    print(contenido)

{'version': '1.5.0', 'autor': 'mindicador.cl', 'fecha': '2019-08-14T01:00:00.000Z', 'uf': {'codigo': 'uf', 'nombre': 'Unidad de fomento (UF)', 'unidad_medida': 'Pesos', 'fecha': '2019-08-13T04:00:00.000Z', 'valor': 27960.63}, 'ivp': {'codigo': 'ivp', 'nombre': 'Indice de valor promedio (IVP)', 'unidad_medida': 'Pesos', 'fecha': '2019-08-13T04:00:00.000Z', 'valor': 29067.31}, 'dolar': {'codigo': 'dolar', 'nombre': 'Dólar observado', 'unidad_medida': 'Pesos', 'fecha': '2019-08-13T04:00:00.000Z', 'valor': 716.69}, 'dolar_intercambio': {'codigo': 'dolar_intercambio', 'nombre': 'Dólar acuerdo', 'unidad_medida': 'Pesos', 'fecha': '2014-11-13T03:00:00.000Z', 'valor': 758.87}, 'euro': {'codigo': 'euro', 'nombre': 'Euro', 'unidad_medida': 'Pesos', 'fecha': '2019-08-13T04:00:00.000Z', 'valor': 803.73}, 'ipc': {'codigo': 'ipc', 'nombre': 'Indice de Precios al Consumidor (IPC)', 'unidad_medida': 'Porcentaje', 'fecha': '2019-07-01T04:00:00.000Z', 'valor': 0.2}, 'utm': {'codigo': 'utm', 'nombre': 'U

In [52]:
for element in contenido:
    pprint(element)
    pprint(contenido[element])

'version'
'1.5.0'
'autor'
'mindicador.cl'
'fecha'
'2019-08-14T01:00:00.000Z'
'uf'
{'codigo': 'uf',
 'fecha': '2019-08-13T04:00:00.000Z',
 'nombre': 'Unidad de fomento (UF)',
 'unidad_medida': 'Pesos',
 'valor': 27960.63}
'ivp'
{'codigo': 'ivp',
 'fecha': '2019-08-13T04:00:00.000Z',
 'nombre': 'Indice de valor promedio (IVP)',
 'unidad_medida': 'Pesos',
 'valor': 29067.31}
'dolar'
{'codigo': 'dolar',
 'fecha': '2019-08-13T04:00:00.000Z',
 'nombre': 'Dólar observado',
 'unidad_medida': 'Pesos',
 'valor': 716.69}
'dolar_intercambio'
{'codigo': 'dolar_intercambio',
 'fecha': '2014-11-13T03:00:00.000Z',
 'nombre': 'Dólar acuerdo',
 'unidad_medida': 'Pesos',
 'valor': 758.87}
'euro'
{'codigo': 'euro',
 'fecha': '2019-08-13T04:00:00.000Z',
 'nombre': 'Euro',
 'unidad_medida': 'Pesos',
 'valor': 803.73}
'ipc'
{'codigo': 'ipc',
 'fecha': '2019-07-01T04:00:00.000Z',
 'nombre': 'Indice de Precios al Consumidor (IPC)',
 'unidad_medida': 'Porcentaje',
 'valor': 0.2}
'utm'
{'codigo': 'utm',
 'fecha'

Consultando por tipo de indicador económico dado un año determinado con api -> https://mindicador.cl/api/{tipo_indicador}/{yyyy}
<p>Con la cual haremos consulta de la paridad EUR/CLP durante el presente año</p>

In [53]:
euro2019 = r.get("https://mindicador.cl/api/euro/2019")

In [54]:
print(euro2019.status_code)

200


Obteniendo data unica del Euro

In [55]:
if euro2019.status_code == 200:
    contenidoeuro = euro2019.json()
    print(contenidoeuro)

{'version': '1.5.0', 'autor': 'mindicador.cl', 'codigo': 'euro', 'nombre': 'Euro', 'unidad_medida': 'Pesos', 'serie': [{'fecha': '2019-08-13T04:00:00.000Z', 'valor': 803.73}, {'fecha': '2019-08-12T04:00:00.000Z', 'valor': 797.8}, {'fecha': '2019-08-09T04:00:00.000Z', 'valor': 795.19}, {'fecha': '2019-08-08T04:00:00.000Z', 'valor': 806.09}, {'fecha': '2019-08-07T04:00:00.000Z', 'valor': 801.91}, {'fecha': '2019-08-06T04:00:00.000Z', 'valor': 808.45}, {'fecha': '2019-08-05T04:00:00.000Z', 'valor': 789.97}, {'fecha': '2019-08-02T04:00:00.000Z', 'valor': 781.12}, {'fecha': '2019-08-01T04:00:00.000Z', 'valor': 778.69}, {'fecha': '2019-07-31T04:00:00.000Z', 'valor': 780.79}, {'fecha': '2019-07-30T04:00:00.000Z', 'valor': 776.85}, {'fecha': '2019-07-29T04:00:00.000Z', 'valor': 775.14}, {'fecha': '2019-07-26T04:00:00.000Z', 'valor': 773.78}, {'fecha': '2019-07-25T04:00:00.000Z', 'valor': 770.15}, {'fecha': '2019-07-24T04:00:00.000Z', 'valor': 771.24}, {'fecha': '2019-07-23T04:00:00.000Z', 'val

data Euro

In [56]:
for elemento in contenidoeuro:
    pprint(elemento)
    pprint(contenidoeuro[elemento])

'version'
'1.5.0'
'autor'
'mindicador.cl'
'codigo'
'euro'
'nombre'
'Euro'
'unidad_medida'
'Pesos'
'serie'
[{'fecha': '2019-08-13T04:00:00.000Z', 'valor': 803.73},
 {'fecha': '2019-08-12T04:00:00.000Z', 'valor': 797.8},
 {'fecha': '2019-08-09T04:00:00.000Z', 'valor': 795.19},
 {'fecha': '2019-08-08T04:00:00.000Z', 'valor': 806.09},
 {'fecha': '2019-08-07T04:00:00.000Z', 'valor': 801.91},
 {'fecha': '2019-08-06T04:00:00.000Z', 'valor': 808.45},
 {'fecha': '2019-08-05T04:00:00.000Z', 'valor': 789.97},
 {'fecha': '2019-08-02T04:00:00.000Z', 'valor': 781.12},
 {'fecha': '2019-08-01T04:00:00.000Z', 'valor': 778.69},
 {'fecha': '2019-07-31T04:00:00.000Z', 'valor': 780.79},
 {'fecha': '2019-07-30T04:00:00.000Z', 'valor': 776.85},
 {'fecha': '2019-07-29T04:00:00.000Z', 'valor': 775.14},
 {'fecha': '2019-07-26T04:00:00.000Z', 'valor': 773.78},
 {'fecha': '2019-07-25T04:00:00.000Z', 'valor': 770.15},
 {'fecha': '2019-07-24T04:00:00.000Z', 'valor': 771.24},
 {'fecha': '2019-07-23T04:00:00.000Z', '

Almacenando en Data Frame "frameEuro", data de la serie de valor del Euro, con parámetros de fecha y valor(CLP)

In [57]:
frameEuro = pd.DataFrame(contenidoeuro['serie'])

In [58]:
print(frameEuro)

                        fecha   valor
0    2019-08-13T04:00:00.000Z  803.73
1    2019-08-12T04:00:00.000Z  797.80
2    2019-08-09T04:00:00.000Z  795.19
3    2019-08-08T04:00:00.000Z  806.09
4    2019-08-07T04:00:00.000Z  801.91
5    2019-08-06T04:00:00.000Z  808.45
6    2019-08-05T04:00:00.000Z  789.97
7    2019-08-02T04:00:00.000Z  781.12
8    2019-08-01T04:00:00.000Z  778.69
9    2019-07-31T04:00:00.000Z  780.79
10   2019-07-30T04:00:00.000Z  776.85
11   2019-07-29T04:00:00.000Z  775.14
12   2019-07-26T04:00:00.000Z  773.78
13   2019-07-25T04:00:00.000Z  770.15
14   2019-07-24T04:00:00.000Z  771.24
15   2019-07-23T04:00:00.000Z  771.79
16   2019-07-22T04:00:00.000Z  769.10
17   2019-07-19T04:00:00.000Z  769.27
18   2019-07-18T04:00:00.000Z  765.26
19   2019-07-17T04:00:00.000Z  764.92
20   2019-07-15T04:00:00.000Z  767.49
21   2019-07-12T04:00:00.000Z  769.14
22   2019-07-11T04:00:00.000Z  771.24
23   2019-07-10T04:00:00.000Z  772.20
24   2019-07-09T04:00:00.000Z  769.13
25   2019-07

frameEuro['valor'][0] -> Index 0 corresponderá al valor del Euro en CLP más actualizado obtenido de la consulta de la API

In [59]:
frameEuro['valor'][0]

803.73

###### Configurando conexión de BBDD en Localhost</p>
Según definición en la actividad anterior, realizada en clases, se decidió realizar el almacenamiento de datos en una base relacional (estrucurada) con motor de bbdd MYSQL, ya que, por la envergadura del ejercicio, dedicimos trabajar con 3 entidades (Equipos, Jugadores, Moneda). El objetivo es poder llevar la información monetarias ya sea de los equipos y/o jugadores a valor en CLP.</p>
La estructura de la Base de Datos relacional se encuentra en el script adjunto -> **"MoneyFootball.sql"**

In [61]:
# Configurando Conxión de BBDD ("moneyfootball") en servidor local ("localhost") con user y pasword ->"root"
# Abriendo conexion con la base de datos
db = pymysql.connect("localhost","root","root","moneyfootball")

# preparando un objeto cursor con metodo cursor()
cursor = db.cursor()

# con ciclo for para el insert de la data del data frame "frameEquipos" en la tabla respectiva
for i in range(0,len(frameEquipos)):
   
    # Preparando SQL query para el INSERT de los records de equipos
    sqlEquipo = "INSERT INTO equipos (nombre_equipo, titulos, ranking, pais) VALUES \
       ('"+frameEquipos["team"][i]+"', "+str(frameEquipos["titles"][i])+", "+str(frameEquipos["pos"][i])+",'"+frameEquipos["country"][i]+"');"

    try:
       # Ejecucioón de la query
       cursor.execute(sqlEquipo)
       # Commit de los cambios en la base de datos
       db.commit()
    except:
       # Rollback en caso cualquier error
       db.rollback()


# Preparando SQL query para el INSERT de record de valor de Euro
sqlEuro = "INSERT INTO monedas (valor_euro) VALUES ("+str(frameEuro['valor'][0])+");"

try:
   # Ejecución de la query
    cursor.execute(sqlEuro)
    # Commit de los cambios en la base de datos
    db.commit()
except:
    # Rollback en caso cualquier error
    db.rollback()

# Preparando SQL query para el INSERT de records de jugadores.
# La estructura de la tabla equipos, hace que el "IdEquipo" coincida con el "ranking" y para el caso del insert de
# data, ambos coinciden con Money_FootBall['pos']. Dado lo anterior el insert de jugadores queda de la siguiente 
# manera:

# con ciclo for para el insert de la data del data frame "Money_FootBall" en la tabla jugadores
for j in range(0,len(Money_FootBall)):
    
    # Para el insert de los jugadores, se dejará como constante el fk IdMoneda (1), ya que se leerá sólo el
    # valor más actualizado, para simplificar la ejecución del ejercicio.
    sqlJugadores = "INSERT INTO jugadores (nombre, nacionalidad, valor_mercado, salario, clausula_contrato, \
        IdEquipo, IdMoneda) VALUES ('"+Money_FootBall['Name'][j]+"', '"+Money_FootBall['Nationality'][j]+"', \
        "+str(Money_FootBall['Value(€)'][j])+", "+str(Money_FootBall['Wage(€)'][j])+", \
        "+str(Money_FootBall['Release Clause(€)'][j])+", "+str(Money_FootBall['pos'][j])+", 1)"

    try:
        cursor.execute(sqlJugadores)
        db.commit()
    
    except:
        db.rollback()
               
# desconección del servidor
db.close()

##### Probando estructura y reglas de negocio en BBDD "moneyfootball"

Lectura data de tabla "equipos"

In [62]:
db = pymysql.connect("localhost","root","root","moneyfootball")

cursor = db.cursor()

sqlReadEquipos = "SELECT idEquipo, nombre_equipo FROM equipos"

cursor.execute(sqlReadEquipos)

# Obteniendo todas las filas en una lista de listas.
results = cursor.fetchall()
for row in results:
    idEquipo = row[0]
    nombre_equipo = row[1]
    
    # Print del resultado obtenido
    print ("idEquipo = {0}, nombre_equipo = {1}".format(idEquipo,nombre_equipo))

db.close()

idEquipo = 1, nombre_equipo = Real Madrid
idEquipo = 2, nombre_equipo = FC Barcelona
idEquipo = 3, nombre_equipo = FC Bayern München
idEquipo = 4, nombre_equipo = Manchester United
idEquipo = 5, nombre_equipo = Juventus
idEquipo = 6, nombre_equipo = Arsenal
idEquipo = 7, nombre_equipo = FC Porto
idEquipo = 8, nombre_equipo = Chelsea
idEquipo = 9, nombre_equipo = Milan
idEquipo = 10, nombre_equipo = Olympique Lyonnais
idEquipo = 11, nombre_equipo = Liverpool
idEquipo = 12, nombre_equipo = Inter
idEquipo = 13, nombre_equipo = Borussia Dortmund
idEquipo = 14, nombre_equipo = Paris Saint-Germain
idEquipo = 15, nombre_equipo = Ajax
idEquipo = 16, nombre_equipo = Valencia
idEquipo = 17, nombre_equipo = Atlético Madrid
idEquipo = 18, nombre_equipo = Roma
idEquipo = 19, nombre_equipo = Olympiacos CFP
idEquipo = 20, nombre_equipo = SL Benfica


Jugadores por Equipo y  Nacionalidad

In [63]:
db = pymysql.connect("localhost","root","root","moneyfootball")

cursor = db.cursor()

sql = "SELECT nombre, nacionalidad, nombre_equipo FROM jugadores j, equipos e where j.IdEquipo = e.IdEquipo"

cursor.execute(sql)

# Obteniendo todas las filas en una lista de listas.
results = cursor.fetchall()
for row in results:
    Nombre_Jugador = row[0]
    Nacionalidad = row[1]
    Equipo = row[2]
    
    # Print del resultado obtenido
    print ("Nombre_Jugador = {0}, Nacionalidad = {1}, Equipo = {2}".format(Nombre_Jugador,Nacionalidad,Equipo))

db.close()

Nombre_Jugador = L. Modrić, Nacionalidad = Croatia, Equipo = Real Madrid
Nombre_Jugador = Sergio Ramos, Nacionalidad = Spain, Equipo = Real Madrid
Nombre_Jugador = T. Kroos, Nacionalidad = Germany, Equipo = Real Madrid
Nombre_Jugador = T. Courtois, Nacionalidad = Belgium, Equipo = Real Madrid
Nombre_Jugador = Casemiro, Nacionalidad = Brazil, Equipo = Real Madrid
Nombre_Jugador = Isco, Nacionalidad = Spain, Equipo = Real Madrid
Nombre_Jugador = Marcelo, Nacionalidad = Brazil, Equipo = Real Madrid
Nombre_Jugador = G. Bale, Nacionalidad = Wales, Equipo = Real Madrid
Nombre_Jugador = K. Navas, Nacionalidad = Costa Rica, Equipo = Real Madrid
Nombre_Jugador = R. Varane, Nacionalidad = France, Equipo = Real Madrid
Nombre_Jugador = Marco Asensio, Nacionalidad = Spain, Equipo = Real Madrid
Nombre_Jugador = K. Benzema, Nacionalidad = France, Equipo = Real Madrid
Nombre_Jugador = Carvajal, Nacionalidad = Spain, Equipo = Real Madrid
Nombre_Jugador = Lucas Vázquez, Nacionalidad = Spain, Equipo = Re

Valor de Mercado de Jugadores por Equipo y Nacionalidad

In [64]:
db = pymysql.connect("localhost","root","root","moneyfootball")

cursor = db.cursor()

sql = "SELECT nombre, nacionalidad, nombre_equipo, valor_mercado, valor_euro, round(valor_mercado*valor_euro,2) \
        FROM jugadores j, equipos e, monedas m where j.IdEquipo = e.IdEquipo and j.IdMoneda = m.IdMoneda"

cursor.execute(sql)

# Obteniendo todas las filas en una lista de listas.
results = cursor.fetchall()
for row in results:
    Nombre_Jugador = row[0]
    Nacionalidad = row[1]
    Equipo = row[2]
    Valor_Euro = row[3]
    Euro_CLP = row[4]
    Valor_CLP = row[5]
    
    # Print del resultado obtenido
    print ("Nombre_Jugador = {0}, Nacionalidad = {1}, Equipo = {2}, Valor_Euro = {3}, Euro_CLP = {4}, \
            Valor_CLP = {5}".format(Nombre_Jugador,Nacionalidad,Equipo,Valor_Euro,Euro_CLP,Valor_CLP))

db.close()

Nombre_Jugador = L. Messi, Nacionalidad = Argentina, Equipo = FC Barcelona, Valor_Euro = 110500000, Euro_CLP = 803.73,             Valor_CLP = 88812162841.8
Nombre_Jugador = L. Suárez, Nacionalidad = Uruguay, Equipo = FC Barcelona, Valor_Euro = 80000000, Euro_CLP = 803.73,             Valor_CLP = 64298398437.5
Nombre_Jugador = M. ter Stegen, Nacionalidad = Germany, Equipo = FC Barcelona, Valor_Euro = 58000000, Euro_CLP = 803.73,             Valor_CLP = 46616338867.19
Nombre_Jugador = Sergio Busquets, Nacionalidad = Spain, Equipo = FC Barcelona, Valor_Euro = 51500000, Euro_CLP = 803.73,             Valor_CLP = 41392093994.14
Nombre_Jugador = Coutinho, Nacionalidad = Brazil, Equipo = FC Barcelona, Valor_Euro = 69500000, Euro_CLP = 803.73,             Valor_CLP = 55859233642.58
Nombre_Jugador = S. Umtiti, Nacionalidad = France, Equipo = FC Barcelona, Valor_Euro = 57000000, Euro_CLP = 803.73,             Valor_CLP = 45812608886.72
Nombre_Jugador = Jordi Alba, Nacionalidad = Spain, Equipo =